In [ ]:
import torch
import torchvision
from PIL import Image

# Create a vector of zeros of size 5
size = (128, 128)
transform = torchvision.transforms.Compose([torchvision.transforms.Resize(size), torchvision.transforms.ToTensor()])
train_dataset = list(torchvision.datasets.Flowers102("/tmp/flowers", "train", transform=transform, download=True))
test_dataset = list(torchvision.datasets.Flowers102("/tmp/flowers", "test", transform=transform, download=True))


def visualize_image(img: torch.Tensor) -> Image.Image:
    return Image.fromarray((img.permute(1, 2, 0) * 255).to(torch.uint8).numpy())


visualize_image(train_dataset[1][0])

In [ ]:
import matplotlib.pyplot as plt

f, ax = plt.subplots(4, 10, figsize=(10, 5))
for i, (im, lbl) in enumerate(list(train_dataset)[:40]):
    ax[i // 10, i % 10].imshow(visualize_image(im))
    ax[i // 10, i % 10].set_title(lbl)
    ax[i // 10, i % 10].axis("off")

In [ ]:
train_images = torch.stack([im for im, _ in train_dataset], dim=0)
train_label = torch.tensor([label for _, label in train_dataset])

In [ ]:
train_images, train_label = train_images.cuda(), train_label.cuda()

In [ ]:

model = torch.nn.Linear(128 * 128 * 3, 102)
model.cuda()

batch_size = 32

loss = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.SGD(model.parameters(), lr=0.0002, momentum=0.9)

for epoch in range(10):
    avg_loss = []

    for i in range(0, len(train_images), batch_size):
        out = model(train_images[i : i + batch_size].view(-1, 128 * 128 * 3))

        optimizer.zero_grad()
        loss_val = loss(out, train_label[i : i + batch_size])
        loss_val.backward()
        optimizer.step()

        avg_loss.append(float(loss_val))

    print(f"Epoch {epoch}, Loss {sum(avg_loss) / len(avg_loss)}")